In [1]:
import os    
from pathlib import Path
import yaml

from jax import numpy as jp
import numpy as np

from mujoco_playground import registry
import mediapy as media

from algorithms.offline.any_percent_bc import get_actor_from_checkpoint, eval_actor
from algorithms.utils.wrapper_gym import GymWrapper

No module named 'flow'
/home/luanagbmartins/miniconda3/envs/d3rl/lib/python3.10/site-packages/glfw/__init__.py:917: GLFWError: (65550) b'X11: The DISPLAY environment variable is missing'
  warnings.warn(message, GLFWError)
No module named 'carla'
No module named 'pybullet_envs'


In [2]:
path_model = "checkpoints/BC/BC-Go1JoystickFlatTerrain-6788a5ea"
with open(os.path.join(path_model, "config.yaml")) as f:
    config = yaml.safe_load(f)

In [3]:
x_vel = 1.0  # @param {type: "number"}
y_vel = 0.0  # @param {type: "number"}
yaw_vel = 0.0  # @param {type: "number"}

command = jp.array([[x_vel, y_vel, yaw_vel]])

In [4]:
env = registry.load(config["env"])
env_cfg = registry.get_default_config(config["env"])
randomizer = registry.get_domain_randomizer(config["env"])

device_rank = int(config["device"].split(":")[-1]) if "cuda" in config["device"] else 0

render_trajectory = []

def render_callback(_, state):
    render_trajectory.append(state)

env_wrapped = GymWrapper(
    env,
    num_actors=1,
    seed=1,
    episode_length=env_cfg.episode_length,
    action_repeat=1,
    render_callback=render_callback,
    randomization_fn=randomizer,
    device_rank=device_rank,
    device=config["device"],
)

state_dim = env_wrapped.observation_space.shape[0]
action_dim = env_wrapped.action_space.shape[0]
max_action = 1.0

Device -- cuda:0
Key device -- {CudaDevice(id=0)}
obs_shape: {'privileged_state': (123,), 'state': (48,)}
Asymmetric observation space
JITing reset and step
Done JITing reset and step


In [5]:
actor = get_actor_from_checkpoint(checkpoint_path=path_model, state_dim=state_dim, action_dim=action_dim, max_action=max_action)

In [6]:
actor.eval()
state, _ = env_wrapped.reset()
env_wrapped.env_state.info["command"] = command
done = False
episode_reward = 0.0
while not done:
    action = actor.act(state, config["device"])
    state, reward, done, _, _ = env_wrapped.step(action)
    env_wrapped.env_state.info["command"] = command
    env_wrapped.render()
    episode_reward += reward

print("Reward: ", episode_reward)

/home/luanagbmartins/Documents/CEIA/offline_to_online/CORL/algorithms/utils/wrapper_gym.py:69: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at /pytorch/torch/csrc/utils/tensor_new.cpp:254.)
  action = torch.tensor([action]).to(self.device)


Reward:  [30.372408]


In [7]:
!export MUJOCO_GL=egl

/home/luanagbmartins/miniconda3/envs/d3rl/lib/python3.10/pty.py:89: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid, fd = os.forkpty()


In [8]:
import mujoco.egl
gl_context = mujoco.egl.GLContext(1024, 1024)
gl_context.make_current()

In [9]:
# Render
scene_option = mujoco.MjvOption()
scene_option.geomgroup[2] = True
scene_option.geomgroup[3] = False
scene_option.flags[mujoco.mjtVisFlag.mjVIS_CONTACTPOINT] = True
scene_option.flags[mujoco.mjtVisFlag.mjVIS_TRANSPARENT] = False
scene_option.flags[mujoco.mjtVisFlag.mjVIS_PERTFORCE] = True

render_every = 2
fps = 1.0 / env.dt / render_every
traj = render_trajectory[::render_every]
frames = env.render(
    traj,
    camera="track",
    height=480,
    width=640,
    scene_option=scene_option,
)

/home/luanagbmartins/miniconda3/envs/d3rl/lib/python3.10/site-packages/glfw/__init__.py:917: GLFWError: (65550) b'X11: The DISPLAY environment variable is missing'
  warnings.warn(message, GLFWError)
/home/luanagbmartins/miniconda3/envs/d3rl/lib/python3.10/site-packages/glfw/__init__.py:917: GLFWError: (65537) b'The GLFW library is not initialized'
  warnings.warn(message, GLFWError)
100%|██████████| 500/500 [00:28<00:00, 17.77it/s]


In [10]:
media.show_video(frames, fps=fps, loop=False)

This browser does not support the video tag.


In [ ]:
media.write_video(os.path.join(path_model, "rollout.mp4"), frames, fps=fps)